# Pedestrian Offline Metric Comparison

In [23]:
"""
Please make sure this notebook is ran using the "Python 2" kernel.
Please save notebooks with important results to your own folder in JupyterHub.

See README for usage instructions:
https://git.zooxlabs.com/zooxco/driving/blob/master/mined_metric/jupyter/README.md
"""
from mined_metric.jupyter.utils.data_access_util import chum_summary_stats, get_validation_data
from mined_metric.jupyter.utils.data_processing_util import (
    parse_meta_data_for_validations,
    create_metric_aggregation_dataframe,
)

VALIDATION_ID = "VALIDATION_ID_PLACEHOLDER"

In [24]:
# Retrieve all data for both experiment and control branches
exp_data_control, exp_data_exp = get_validation_data(VALIDATION_ID)
print("Control Git SHA: {}".format(exp_data_control["experiment"]["gitsha"]))
print("Experiment Git SHA: {}".format(exp_data_exp["experiment"]["gitsha"]))
print("Make sure the control and experiment Git SHAs are not swapped! (If they are, switch them.)")

In [28]:
def remove_variant(chum_uri):
    return chum_uri.split("?")[0]

control_name = exp_data_control["experiment"]["additionalMsg"]
exp_name = exp_data_exp["experiment"]["additionalMsg"]
control_chum_uris = set([remove_variant(x["chum_uri"]) for x in exp_data_control["meta"]])
exp_chum_uris = set([remove_variant(x["chum_uri"]) for x in exp_data_exp["meta"]])

common_chum_uris = control_chum_uris.intersection(exp_chum_uris)

print("control chums:", len(control_chum_uris))
print("exp chums:", len(exp_chum_uris))
print("common chums:", len(common_chum_uris))

def get_results(entries, common_chum_uris):
    value_sums = {}
    processed_entries = 0
    for x in entries:
        if remove_variant(x["chum_uri"]) not in common_chum_uris:
            continue
        processed_entries += 1
        for k, v in x.items():
            if isinstance(v, int) or isinstance(v, float):
                if k not in value_sums:
                    value_sums[k] = 0
                    
                if k == "mean_first_yield_earliness":
                    value_sums[k] += v * x["num_first_yields_for_peds_in_corridor"]
                else:
                    value_sums[k] += v
    return value_sums

control_value_sums = get_results(exp_data_control["meta"], common_chum_uris)
exp_value_sums = get_results(exp_data_exp["meta"], common_chum_uris)

def get_summary(value_sums):
    cw_precision = value_sums["crosswalk_tps"] / (value_sums["crosswalk_tps"] + value_sums["crosswalk_fps"])
    cw_fraction_dropped = value_sums["dropped_crosswalk_tp_yields"] / value_sums["crosswalk_tps"]
    jw_precision = value_sums["jaywalk_tps"] / (value_sums["jaywalk_tps"] + value_sums["jaywalk_fps"])
    jw_fraction_dropped = value_sums["dropped_jaywalk_tp_yields"] / value_sums["jaywalk_tps"]
    recall = value_sums["all_tps"] / value_sums["num_peds_in_corridor"]
    mean_fy_earliness = value_sums["mean_first_yield_earliness"] / value_sums["num_first_yields_for_peds_in_corridor"]
    
    print("cw precision:", cw_precision)
    print("cw fraction dropped:", cw_fraction_dropped)
    print("jw precision:", jw_precision)
    print("jw fraction dropped:", jw_fraction_dropped)
    print("recall:", recall)
    print("mean first yield earliness:", mean_fy_earliness)

print("---- experiment:", control_name)
get_summary(control_value_sums)
control_cw_precision = control_value_sums["crosswalk_tps"] / (control_value_sums["crosswalk_tps"] + control_value_sums["crosswalk_fps"])

print("---- experiment:", exp_name)
get_summary(exp_value_sums)